# Deep Text Corrector

## Overview
While context-sensitive spell-check systems (such as AutoCorrect) are able to automatically correct a large number of input errors in instant messaging, email, and SMS messages, they are unable to correct even simple grammatical errors. For example, the message “I’m going to store” would be unaffected by typical autocorrection systems, when the user most likely intendend to communicate “I’m going to the store”.

Inspired by recent advancements in NLP driven by deep learning (such as those in Neural Machine Translation by Bahdanau et al., 2014), I decided to try training a neural network to solve this problem. Specifically, I set out to construct sequence-to-sequence models capable of processing a sample of conversational written English and generating a corrected version of that sample. In this post I’ll describe how I created this “Deep Text Corrector” system and present some encouraging initial results.

The basic idea behind this project is that we can generate large training datasets for the task of grammar correction by starting with grammatically correct samples and introducing small errors to produce input-output pairs. The details of how we construct these datasets, train models using them, and produce predictions for this task are described below.

## Performance Metrics

categorical_crossentropy loss

## Objective
Given a grammatical wrong sentence following the above pertubation we need to predict the grammatical correct version of it.

In [1]:
#Importing ALl the required modules
from collections import Counter
import nltk
import sys
import os
import nltk
import random
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Reshape,Concatenate
from tensorflow.keras.layers import Embedding, Dense, TimeDistributed
from tensorflow.python.keras.layers import Layer,Attention, AdditiveAttention
from tensorflow.python.keras import backend as K
from tensorflow.python.keras.models import load_model
from tensorflow.keras.utils import to_categorical
from tensorflow.python.keras.models import load_model
from tqdm import tqdm
from random import randint
nltk.download('averaged_perceptron_tagger')
nltk.download('punkt')
nltk.download('wordnet')
from nltk.translate.bleu_score import corpus_bleu

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     C:\Users\v-pratje\AppData\Roaming\nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\v-pratje\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\v-pratje\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


## Required File Paths

In [2]:
#We have the file path of all the train test files
train_path = "Processed_Datasets/processed_train_data.txt"
val_path = "Processed_Datasets/processed_val_data.txt"
test_path = "Processed_Datasets/processed_test_data.txt"
processed_file_path = "Processed_Datasets/processed_movie_lines.txt"
anon_clara = "Novel_Datasets/Anon_Clara_1864.txt"
Wcollins_Woman_1860 = "Novel_Datasets/Wcollins_Woman_1860.txt"
Stevenson_Treasure_1883 = "Novel_Datasets/Stevenson_Treasure_1883.txt"
Barclay_Ladies_1917 = "Novel_Datasets/Barclay_Ladies_1917.txt"
Barclay_Postern_1911 = "Novel_Datasets/Barclay_Postern_1911.txt"
Barclay_Rosary_1909 = "Novel_Datasets/Barclay_Rosary_1909.txt"
Bennet_Helen_1910 = "Novel_Datasets/Bennet_Helen_1910.txt"

## EDA - Movies Dialogues
Print top 10 lines of the movies dialogue data set and check for the behaviour

In [3]:
"""
Method to print the top 10 lines of the Cornell Movie Dialogue Corpus
"""
def printtopLines(path):
    with open(path, "r",encoding='iso-8859-1') as raw_data :
        count = 0
        for line in raw_data:
            if(count==100):
                break
            print(line)
            count += 1

In [4]:
#Printing top 10 lines of the Cornell Movie Corpus
printtopLines(anon_clara)

ï»¿CLARA VAUGHAN

BOOK I.

CHAPTER I.

I do not mean to describe myself. Already I feel that the personal pronoun will appear too often in these pages. Knowing the faults of my character almost as well as my best friends know them, I shall attempt to hide them no more than would those beloved ones. Enough of this: the story I have to tell is strange, and short as my own its preamble.

The day when I was ten years old began my serious life. It was the 30th of December, 1842; and proud was the kiss my loving father gave me for spelling, writing, and pronouncing the date in English, French, and Italian. No very wonderful feat, it is true, for a clever child well-taught; but I was by no means a clever child; and no one except my father could teach me a single letter. When, after several years of wedlock, my parents found new joy in me, their bliss was soon overhung with care. They feared, but durst not own the fear, lest the wilful, passionate, loving creature, on whom their hearts were wh

#### Conculsion
1. The data are present in the format of dialogue
2. Every individual dialogue is present with their corresponding charaters in movies with dialogue numbers and 'dolar' signs<br />
3. We need to clear all the unwanted dialogue numbers and 'dolar' signs and keep only the English sentences. <br />
4. We need to give a space between all the 'Auxiliary verb' and the corresponding words. **Ex. I've should present as I 've as we will be prediticting auxiliary verb also.** This can be done using nltk word tokenizer.<br /> 

## Pre Processing

In [5]:
"""
1. Getting pure english sentences from the Cornell data set by removing the unwanted characters
2. Giving space between auxiliary verb and the corrsponding words
3. Storing the pre processed dailogues into processed_movie_lines.txt
"""
def preprocessing(path,out):
     with open(path, "r",encoding='iso-8859-1') as raw_data:
        for line in raw_data:
            line = line.replace('"','')
            line = line.replace('. . .','')
            line = line.replace('mr.','mr')
            line = line.replace('mrs.','mrs')
            line = line.replace('miss.','miss')
            line = line.replace('dr.','dr')
            line = line.replace('Mr.','Mr')
            line = line.replace('Mrs.','Mrs')
            line = line.replace('Miss.','Miss')
            line = line.replace('Dr.','Dr')
            parts = line.split(".")
            parts = parts[:len(parts)-1]
            part = []
            for sent in parts:
                if '?' in sent and '!' in sent:
                    sent = sent.replace('?','question_sign ?')
                    sent = sent.replace('!','exclaim_sign !')
                    seqs = sent.split("?")
                    for seq in seqs:
                        if '!' in seq:
                            exclaim = seq.split('!')
                            for exc in exclaim:
                                part.append(exc)
                elif '?' in sent:
                    sent = sent.replace('?',' question_sign ?')
                    question_sent = sent.split("?")
                    for ques in question_sent:
                        part.append(ques)
                elif '!' in sent:
                    sent = sent.replace('!',' exclaim_sign !')
                    exclaim_sent = sent.split('!')
                    for ex in exclaim_sent:
                        part.append(ex)
                else:
                    part.append(sent)
                    
            for sentences in part:
                if "question_sign" in sentences:
                    sentences = sentences.replace('question_sign','?')
                elif "exclaim_sign" in sentences:
                    sentences = sentences.replace('exclaim_sign','!')
                else:
                    sentences = sentences + " ."
                s = sentences.strip().lower().encode().decode("utf-8", "ignore")
                preprocessed_line = " ".join(nltk.word_tokenize(s))
                if(len(preprocessed_line)<4):
                    continue
                elif preprocessed_line.startswith("'"):
                    continue
                print(preprocessed_line)
                out.write(preprocessed_line + "\n")

In [6]:
with open(processed_file_path, "w") as out:
    preprocessing(anon_clara,out)
    preprocessing(Wcollins_Woman_1860,out)
    preprocessing(Stevenson_Treasure_1883,out)
    preprocessing(Barclay_Ladies_1917,out)
    preprocessing(Barclay_Postern_1911,out)
    preprocessing(Barclay_Rosary_1909,out)
    preprocessing(Bennet_Helen_1910,out)

book i .
chapter i .
i do not mean to describe myself .
already i feel that the personal pronoun will appear too often in these pages .
knowing the faults of my character almost as well as my best friends know them , i shall attempt to hide them no more than would those beloved ones .
enough of this : the story i have to tell is strange , and short as my own its preamble .
the day when i was ten years old began my serious life .
it was the 30th of december , 1842 ; and proud was the kiss my loving father gave me for spelling , writing , and pronouncing the date in english , french , and italian .
no very wonderful feat , it is true , for a clever child well-taught ; but i was by no means a clever child ; and no one except my father could teach me a single letter .
when , after several years of wedlock , my parents found new joy in me , their bliss was soon overhung with care .
they feared , but durst not own the fear , lest the wilful , passionate , loving creature , on whom their hear

so i hushed him off with a cradle song .
but before the long lashes sunk flat on his cheeks , like the ermine tips on my muff , and while his red lips yet trembled like cherries in the wind , my attention was suddenly drawn to the lake .
there was a plashing , and barking , and hissing , and napping of snow-white wings - poor juan engaged in unequal combat with two fierce swans who had a nest on the island .
the poor little dog , though he fought most gallantly , was soon driven into deep water , and the swans kept knocking him under with rapid and powerful strokes .
seeing him almost drowned , i called clement to save him at once .
i ca n't , said the brave youth ; you go if you like .
they 'll kill me , and i ca n't bear it ; and the water ith tho cold .
in a moment i pushed off the boat which was near , jumped into it , and , seizing an oar , contrived to beat back the swans , and lifted the poor little dog on board , gasping , half-drowned , and woefully beaten .
meanwhile my lord 

between the two fears he chose the less , and followed me to my father 's grave .
i stood there and angrily waved him back , but he still persisted , though trembling .
cousin clara , he said - and his lisp was quite gone , and he tried to be in a passion - cousin clara , you shall hear what i have got to say .
you have lived with me now a long time , and i 'm sure we have agreed very well , and i - i - no , i do n't see why we should not be married .
perhaps , he continued , you are afraid that i do n't care about you .
really now , i often think that you would be very good-looking , if you would only laugh now and then , and leave off those nasty black gowns ; and then if you would only leave off being so grand , and mysterious , and stately , and getting up so early , i would let you do as you liked , and you might paint me and have a lock of my hair .
yes , he replied , turning pale , and inclined to fly .
there 's water enough there now .
if you ever dare again to say one word lik

gude art alaive , if e bai n't a spurrity maid .
but if ere a chap zays the black word on e - and thiccy 's the taime when a maid ca n't help herzell , then ony you karl jan uxtable that 's arl my dear , and if so be it 's in the dead hoor of the naight , and thee beest to tother zaide of hexymoor , ai 'll be by the zaide of thee zooner nor ai could thraw a vorehip .
before i could thank him for his honest championship my mother entered the room , and all his bashfulness lost for the moment in the pride of strength came over him again like an extinguisher .
although he did not tremble - his nerves were too firm for that - he stood fumbling with his hat , and reddening , and looking vaguely about , at a loss where to put his eyes or anything else .
my mother , quite worn out with her morning 's walk , surprised at her uncouth visitor , and frightened perhaps at his bulk , sank on our new-fangled sofa , in a stupor of weakness .
then it was strange and fine to see the strong man 's sense

in an agony of tears , i knelt by the side of the bed , watching her placid and deathlike face .
till then i had never known how strongly and deeply i loved her .
i firmly believe that she was revived in some degree by the glare of the patched quilt upon her eyes .
the antagonism of nature was roused , and brought home her wandering powers .
yes , mother ; here i am , with my own dear mother .
she opened her arms , and held me in a nervous cold embrace , and thanked god , and wept .
chapter xvii .
when the surgeon came , he pronounced that none of her limbs were broken , but that the shock to the brain , and the whole system , had been so severe , that the only chance of recovery consisted in perfect quiet .
she herself said that the question was , whether providence wanted her still to watch over her child .
after some days she came down stairs , not without my support , and was propped once more upon her poor sofa .
calm she appeared , and contented , and happy in such sort as of old

...

for a dog-cart stopped in front of the house at that precise second , deposited a lady of commanding mien , and dashed off again .
the lady opened james 's gate and knocked at james 's front door .
she could not be a relative of a tenant .
james was closely acquainted with all his tenants , and he had none of that caliber .
moreover , helen had caused a small board to be affixed to the gate : tenants will please go round to the back .
bless us !
he murmured , angrily .
and , by force of habit , he went and opened the door .
then he recognised the lady .
it was sarah swetnam , eldest child of the large and tumultuously intellectual swetnam family that lived in a largish house in a largish way higher up the road , and as to whose financial stability rumour always had something interesting to say .
in the very nick of time he slipped aside , and thus avoided the inconvenience of being crushed to pulp between two locomotives under full steam .
it appeared that they had not met for some yea

the winks were without doubt an expression of sentiments aroused by the solemnity of emanuel 's frown .
the piano tinkled on , and then emanuel 's face was observed to change .
the frown vanished and a smile of heavenly rapture took its place .
his mouth gradually opened till its resemblance to the penultimate vowel was quite realistic , and simultaneously , by a curious muscular co-ordination , he rose on his toes to a considerable height in the air .
the strain was terrible - like waiting for a gun to go off .
james was conscious of a strange vibration by his side , and saw that jos swetman had got the whole of a lace handkerchief into her mouth .
the gun went off - not with a loud report , but with a gentle and lofty tenor piping , somewhere in the neighbourhood of f , or it might have been only e though , indeed , a .
photograph would have suggested that emanuel was singing at lowest the upper c , and the performer slowly resumed his normal stature .
o love !
he had exclaimed , ada

all right , he said .
the porter touched his cap .
label that luggage for crewe , he whispered to the porter , and passed straight on , as if taking exercise on the platform .
yes , sir , said the porter .
when he got back to helen of course he had to make conversation with a nonchalant air , in order to hide his guilty feelings .
so none of 'em has come to see you off !
he observed .
none o ' yer friends .
no fear !
she said .
i would n't have it for anything .
railway station .
never had any , he said .
the train was prompt , but between shawport and crewe it suffered delays , so that there was not an inordinate amount of time to spare at the majestic junction .
heedless , fly-away creature that she was , helen scurried from the north stafford platform to the main-line platform without a thought as to her luggage .
she was apparently so preoccupied with her handbag , which contained her purse , that she had no anxiety left over for her heavy belongings .
as they hastened forward , he

i 'm calling on the swetnams the day after to-morrow .
i 'll tell them about - about to-day , and when mrs swetnam asks me for an explanation of it , i will be mysterious .
if lilian is there , mrs swetnam will certainly get her out of the room .
then i will just give the faintest hint that the explanation is merely jealousy between emanuel and mr dean concerning - a certain young lady .
i shall treat it all as a joke ; you can rely on me .
immediately i am gone lilian will hear about it .
she smiled the arch , naughty , pleasantly-malign smile of a terribly experienced dowager .
and she seemed positively anxious that james should have andrew dean for a son-in-law .
james , in his simplicity , was delighted .
it appeared to him a mephistophelian ingenuity .
he thought how clever women were , on their own ground , and what an advantage they had in their immense lack of scruple .
of course , said she , i have always said that a marriage between andrew dean and lilian would be a mistake -

james , she exclaimed , you 've told her .
and you promised you would n't till to-morrow .
nay !
said james .
told me what , mrs prockter ?
helen asked , utterly unexpectant of the answer she was to get .
my dear girl , said the elder dame , do not call me mrs prockter .
i am mrs ollerenshaw .
i am the property that your uncle has been buying at derby .
and he is my sick relative at nottingham .
we preferred to do it like that .
we could not have survived engagements and felicitations .
oh , you wicked sinners !
you - you terrible darlings !
helen burst out as soon as she could control her voice .
mrs ollerenshaw wept discreetly .
bless us !
bless us !
murmured james , not to beseech a benediction , but simply to give the impression quite false that , in his opinion , much fuss was being made about nothing .
the new scale of existence was definitely accepted .
and in private mrs ollerenshaw entirely agreed with helen as to the merits of the butler .
after dinner james hurried to his la

### Movies Dialogues after Pre Processing

In [7]:
#Printing the top 10 lines after pre processing the Cornell Movie Corpus
#All the unwanted special characters with dialogue numbers should be removed and auxiliary verb should be seprated from the corresponding wordds
printtopLines(processed_file_path)

book i .

chapter i .

i do not mean to describe myself .

already i feel that the personal pronoun will appear too often in these pages .

knowing the faults of my character almost as well as my best friends know them , i shall attempt to hide them no more than would those beloved ones .

enough of this : the story i have to tell is strange , and short as my own its preamble .

the day when i was ten years old began my serious life .

it was the 30th of december , 1842 ; and proud was the kiss my loving father gave me for spelling , writing , and pronouncing the date in english , french , and italian .

no very wonderful feat , it is true , for a clever child well-taught ; but i was by no means a clever child ; and no one except my father could teach me a single letter .

when , after several years of wedlock , my parents found new joy in me , their bliss was soon overhung with care .

they feared , but durst not own the fear , lest the wilful , passionate , loving creature , on whom 

#### Conclusion
1. All the unwanted characters like 'dolar' with their respective dialogue numbers.
2. All the auxiliary verbs like **'s,'m,'re** are spearated from their respective words by a space using nltk word tokenizer

## Create Train Validation Sets
We will use 80:20 ration for train and validation datasets from the pre processed movie dialogue corpus

In [3]:
#Get total Number of lines in a file
def gettotalLines(path):
  with open(path, "r") as processed_file:
    count = 0
    for line in processed_file:
      count += 1
  return count

In [9]:
#Create the train test sets(80% train and 20% test/validation)
#Saving train set to processed_train_data.txt
#Saving validation set to processed_test_data.txt
def createtraintestsets():
    """
    Method to create train and validation sets
    """
    numOfLines = gettotalLines(processed_file_path)
    numOfTrainSet = 0.8 * numOfLines
    count = 0
    with open(processed_file_path, "r") as processed_data, open(train_path, "w") as train, open(val_path, "w") as val, open(test_path, "w") as test:
        for line in processed_data:
            if count < numOfTrainSet:
                train.write(line)
            else:
                if count < 0.9 * numOfLines:
                    val.write(line)
                else:
                    test.write(line)
            count += 1

In [10]:
createtraintestsets()

In [11]:
print("Size of processed data is: ",gettotalLines(processed_file_path))
print("Size of train data is: ",gettotalLines(train_path))
print("Size of validate data is: ",gettotalLines(val_path))
print("Size of validate data is: ",gettotalLines(test_path))

Size of processed data is:  44616
Size of train data is:  35693
Size of validate data is:  4462
Size of validate data is:  4461


#### Observations
We have train and validation data in the processed_train_data.txt and processed_test_data.txt respectively.

### Train Set

In [12]:
printtopLines(train_path)

book i .

chapter i .

i do not mean to describe myself .

already i feel that the personal pronoun will appear too often in these pages .

knowing the faults of my character almost as well as my best friends know them , i shall attempt to hide them no more than would those beloved ones .

enough of this : the story i have to tell is strange , and short as my own its preamble .

the day when i was ten years old began my serious life .

it was the 30th of december , 1842 ; and proud was the kiss my loving father gave me for spelling , writing , and pronouncing the date in english , french , and italian .

no very wonderful feat , it is true , for a clever child well-taught ; but i was by no means a clever child ; and no one except my father could teach me a single letter .

when , after several years of wedlock , my parents found new joy in me , their bliss was soon overhung with care .

they feared , but durst not own the fear , lest the wilful , passionate , loving creature , on whom 

### Validation Set

In [13]:
printtopLines(val_path)

but from garth , at that moment , it did not sound commonplace to jane , and she answered it quite frankly and fully .

she wanted above all things to tell him exactly how she did ; to hear all about himself , and compare notes on the happenings of these three interminable days ; and to take up their close comradeship again , exactly where it had left off .

her hand went home to his with that firm completeness of clasp , which always made a hand shake with jane such a satisfactory and really friendly thing .

very fit , thank you , dal , she answered .

at least i am every moment improving in health and spirits , now i have arrived here at last .

garth stood his racket against the arm of her chair and deposited himself full length on the grass beside her , leaning on his elbow .

was anything wrong with london ?

he asked , rather low , not looking up at her , but at the smart brown shoe , planted firmly on the grass so near his hand .

nothing was wrong with london , replied jane fr

### Test Set

In [14]:
printtopLines(test_path)

yes , i remember .

about little mrs fussy .

well all the women had gone up to dress for dinner ; excepting jane , who never needed more than half an hour ; and fussy , who was being sprightly , in a laboured way ; and fancied herself the centre of attraction which kept us congregated in the hall .

as a matter of fact , we were waiting to tell jane some private news we had just heard about a young chap in the guards , who was in fearful hot water for ragging .

his colonel was an old friend of jane 's , and we thought she could put in a word , and improve matters for billy .

so mrs fussy was very much de trop , and did n't know it .

jane was sitting with her back to all of us , her feet on the fender , and her skirt turned up over her knees .

oh , there was another one , underneath ; a handsome silk thing , with rows of little frills , which you would think should have gone on outside .

but jane 's best things are never paraded ; always hidden .

i do n't mean clothes , now ; but

## Choosing Vocabulary
1. As we are doing deep text correction we can use a small vocabulary as grammatical words are the most frequent words in any corpus<br />
2. Here we will use a vocabulary of size 2000

In [3]:
# https://www.geeksforgeeks.org/use-yield-keyword-instead-return-keyword-python/
def read_tokens(path):
    """
    1. Method to return all the tokens in each sentence.
    2. A list of token is returned for each sentence in the respective text file
    3. yield is used in place of return in order to keep on returning tokens till the end of the text file
    :param path: path of the text file
    :return: list of tokens for each sentence or line in the file
    """
    with open(path, "r") as f:
        for line in f:
            yield line.lower().strip().split()

### Setting Fixed Tokens
We have 4 fixed tokens which are generic -
1. PAD - It is the zero padding token which will be used to balance the sentence sizes
2. GO - It is the start of sentence token which will be assigned to decoder inputs
3. EOS - It is the end of sentence token which will be assigned to decoder inputs and used during decoding
4. UNK - It is the unknow token used for the tokens not present in the vocabulary

In [4]:
#Setting the fixed tokens to be used
PAD_ID = 0
GO_ID = 1
EOS_ID = 2
PAD_TOKEN = "PAD"
EOS_TOKEN = "EOS"
GO_TOKEN = "GO"
UNKNOWN_TOKEN = "UNK"
special_tokens = [PAD_TOKEN,GO_TOKEN,EOS_TOKEN,UNKNOWN_TOKEN]

### Tokenizing
1. Here we choose the top 2000 words that occurred in our pre processed corpus and set it as our vocabulary<br />
2. We append the special character at the start of the vocabulary.<br />
3. We create id for each tokens.<br />

In [5]:
#Create a counter
token_counts = Counter()

#Get the count of occurance of all the words present in our pre processed corpus
for tokens in read_tokens(processed_file_path):
    token_counts.update(tokens)

#Sort the token according to their count of occurance in the pre processed corpus
count_pairs = sorted(token_counts.items(),key=lambda x: (-x[1], x[0]))

#Select all the words from the count pairs in the sorted orders
vocabulary, _ = list(zip(*count_pairs))
vocabulary = list(vocabulary)

# Insert all  the special tokens at the beginning.
vocabulary[0:0] = special_tokens
vocabulary = vocabulary

#Assigne id to each token as per the vocabulary
full_token_and_id = zip(vocabulary, range(len(vocabulary)))

#Create dictionary variables which can contain both id to token and token to id representation
token_to_id = dict(full_token_and_id)
id_to_token = {v: k for k, v in token_to_id.items()}

In [6]:
len(vocabulary)

24644

In [7]:
token_to_id

{'PAD': 0,
 'GO': 1,
 'EOS': 2,
 'UNK': 3,
 ',': 4,
 'the': 5,
 '.': 6,
 'and': 7,
 'to': 8,
 'of': 9,
 'i': 10,
 'a': 11,
 'in': 12,
 'was': 13,
 'her': 14,
 'it': 15,
 'he': 16,
 'that': 17,
 'my': 18,
 'had': 19,
 'you': 20,
 'she': 21,
 'his': 22,
 'as': 23,
 'with': 24,
 'me': 25,
 'for': 26,
 ';': 27,
 'at': 28,
 'not': 29,
 'on': 30,
 "'s": 31,
 'but': 32,
 'have': 33,
 'be': 34,
 'him': 35,
 'all': 36,
 'is': 37,
 'from': 38,
 'which': 39,
 'by': 40,
 'so': 41,
 'said': 42,
 'this': 43,
 'no': 44,
 'when': 45,
 'if': 46,
 'one': 47,
 'we': 48,
 '!': 49,
 'would': 50,
 'there': 51,
 'were': 52,
 'could': 53,
 'they': 54,
 'been': 55,
 'do': 56,
 'now': 57,
 '?': 58,
 'then': 59,
 'your': 60,
 'or': 61,
 'what': 62,
 'out': 63,
 'them': 64,
 'an': 65,
 'will': 66,
 'more': 67,
 'up': 68,
 'little': 69,
 'time': 70,
 "n't": 71,
 'into': 72,
 'who': 73,
 'man': 74,
 'own': 75,
 'upon': 76,
 'are': 77,
 'before': 78,
 'miss': 79,
 'than': 80,
 'very': 81,
 'only': 82,
 'never': 83,


In [8]:
id_to_token

{0: 'PAD',
 1: 'GO',
 2: 'EOS',
 3: 'UNK',
 4: ',',
 5: 'the',
 6: '.',
 7: 'and',
 8: 'to',
 9: 'of',
 10: 'i',
 11: 'a',
 12: 'in',
 13: 'was',
 14: 'her',
 15: 'it',
 16: 'he',
 17: 'that',
 18: 'my',
 19: 'had',
 20: 'you',
 21: 'she',
 22: 'his',
 23: 'as',
 24: 'with',
 25: 'me',
 26: 'for',
 27: ';',
 28: 'at',
 29: 'not',
 30: 'on',
 31: "'s",
 32: 'but',
 33: 'have',
 34: 'be',
 35: 'him',
 36: 'all',
 37: 'is',
 38: 'from',
 39: 'which',
 40: 'by',
 41: 'so',
 42: 'said',
 43: 'this',
 44: 'no',
 45: 'when',
 46: 'if',
 47: 'one',
 48: 'we',
 49: '!',
 50: 'would',
 51: 'there',
 52: 'were',
 53: 'could',
 54: 'they',
 55: 'been',
 56: 'do',
 57: 'now',
 58: '?',
 59: 'then',
 60: 'your',
 61: 'or',
 62: 'what',
 63: 'out',
 64: 'them',
 65: 'an',
 66: 'will',
 67: 'more',
 68: 'up',
 69: 'little',
 70: 'time',
 71: "n't",
 72: 'into',
 73: 'who',
 74: 'man',
 75: 'own',
 76: 'upon',
 77: 'are',
 78: 'before',
 79: 'miss',
 80: 'than',
 81: 'very',
 82: 'only',
 83: 'never',


#### Observation
As we have selected 2000 words for our vocabulary we got the top 2000 tokens present in our pre processed dialogue corpus with their corresponding ids.


## Structured Data(Building Dataset)
1. Here we will create data set based on size of the sentence. We have 4 buckets size and hence we will classify the data into the buckets they fit. <br />
2. As we will use encoder and decoder model for training, we will create encoder input, decoder input and the target word sequence for our train and validation data set. <br />
3. The train and validation data set will be present in the form of sequence of token id.<br />
4. As per the encoder and decoder model the decoder input same as target sequnce with a start of sentence token at the starting and an end of sentence sequence at the end.
5. We will create grammatical errors in the input sequence for training the datasets with some random probabilities.

In [9]:
#Dataset copies is used to create multiple copies of data from the same processed dataset
dataset_copies = 1

#These two probabilities will be used to create perturbations in the input sentences
dropout_prob= 0.25
replacement_prob= 0.25
verb_replacement_prob = 0.50

max_sent_length = 50
max_vocabulary_size = len(vocabulary)

In [10]:
#Return the token which is not there in vocabulary
def unknown_token():
    """
    Returns the unknown token which is not present in the vocabulary
    """
    return UNKNOWN_TOKEN

In [11]:
#Converts a id to token
def convert_id_to_token(token_id):
    """
    Returns token for the corresponding ids
    """
    return id_to_token[token_id]

In [12]:
#Converts a token to id
def convert_token_to_id(token):
    """
    Returns the id for the corresponding token
    """
    token_with_id = token if token in token_to_id else unknown_token()
    return token_to_id[token_with_id]

### Dropout and Replacement Tokens
In this project we are doing two types of grammar corrections.
One is we will drop some auxiliary verbs(is,the,a,'ve,'ll,'m) randomly and the second one is we will replace some tokens which are wrongly used in the sentences(then->than).
We will introduce 12 grammatical errors in our train and validation data as follows
1. a
2. an
3. the
4. 'll
5. 's
6. 'm
7. 've
8. to
9. there -> their : their -> there
10. then -> than : than -> then
11. is -> was : was -> is
12. here -> hear : hear -> here

In [13]:
#Dropout Tokens
DROPOUT_TOKENS = {"a", "an", "the", "'ll", "'s", "'m", "'ve", "to"}
#Replacement Tokens
REPLACEMENTS = {"there": "their", 
                "their": "there", 
                "then": "than",
                "than": "then",
                "is":"was",
                "was":"is",
                "a":"an",
                "an":"a"}

### Verb Past and Past Participle Tense Replacement Token Using NLTK
Ex. live -> lived;lived -> live and live -> living;living->live

In [14]:
#Printing tokens with their corresponding id for our vocabulary
#https://stackoverflow.com/questions/3753021/using-nltk-and-wordnet-how-do-i-convert-simple-tense-verb-into-its-present-pas
#https://medium.com/@gianpaul.r/tokenization-and-parts-of-speech-pos-tagging-in-pythons-nltk-library-2d30f70af13b
verb_past = {}
verb_present_participle = {}
verb_third_person = {}
from nltk.stem.wordnet import WordNetLemmatizer
for token in tqdm(vocabulary):
    key,value = nltk.pos_tag([token])[0]
    if value == 'VBD':
        base_word = WordNetLemmatizer().lemmatize(key,'v')
        verb_past[key] =  base_word
        verb_past[base_word] = key
    elif value == 'VBG':
        base_word = WordNetLemmatizer().lemmatize(key,'v')
        verb_present_participle[key] =  base_word
        verb_present_participle[base_word] = key
    elif value == 'VBZ':
        base_word = WordNetLemmatizer().lemmatize(key,'v')
        verb_third_person[key] =  base_word
        verb_third_person[base_word] = key

100%|██████████| 24644/24644 [00:30<00:00, 807.55it/s] 


In [15]:
#Printing the verb past replacement list
len(verb_past)

446

In [16]:
verb_past

{'was': 'be',
 'be': 'were',
 'had': 'have',
 'have': 'had',
 'said': 'say',
 'say': 'said',
 'were': 'be',
 'did': 'do',
 'do': 'did',
 'looked': 'look',
 'look': 'looked',
 'came': 'come',
 'come': 'came',
 'went': 'go',
 'go': 'went',
 'seemed': 'seem',
 'seem': 'seemed',
 'took': 'take',
 'take': 'took',
 'turned': 'turn',
 'turn': 'turned',
 'got': 'get',
 'get': 'got',
 'began': 'begin',
 'begin': 'began',
 'fell': 'fell',
 'gave': 'give',
 'give': 'gave',
 'rose': 'rise',
 'rise': 'rose',
 'replied': 'reply',
 'reply': 'replied',
 'walked': 'walk',
 'walk': 'walked',
 'wanted': 'want',
 'want': 'wanted',
 'followed': 'follow',
 'follow': 'followed',
 'appeared': 'appear',
 'appear': 'appeared',
 'stopped': 'stop',
 'stop': 'stopped',
 'happened': 'happen',
 'happen': 'happened',
 'waited': 'wait',
 'wait': 'waited',
 'closed': 'close',
 'close': 'closed',
 'remained': 'remain',
 'remain': 'remained',
 'dropped': 'drop',
 'drop': 'dropped',
 'whispered': 'whisper',
 'whisper': 'w

In [17]:
#Printing the verb past participle replacement list
len(verb_present_participle)

3464

In [18]:
verb_present_participle

{'being': 'be',
 'be': 'being',
 'having': 'have',
 'have': 'having',
 'looking': 'look',
 'look': 'looking',
 'going': 'go',
 'go': 'going',
 'evening': 'even',
 'even': 'evening',
 'coming': 'come',
 'come': 'coming',
 'leaving': 'leave',
 'leave': 'leaving',
 'feeling': 'feel',
 'feel': 'feeling',
 'making': 'make',
 'make': 'making',
 'standing': 'stand',
 'stand': 'standing',
 'waiting': 'wait',
 'wait': 'waiting',
 'taking': 'take',
 'take': 'taking',
 'darling': 'darling',
 'sitting': 'sit',
 'sit': 'sitting',
 'seeing': 'see',
 'see': 'seeing',
 'doing': 'do',
 'do': 'doing',
 'saying': 'say',
 'say': 'saying',
 'thinking': 'think',
 'think': 'thinking',
 'holding': 'hold',
 'hold': 'holding',
 'speaking': 'speak',
 'speak': 'speaking',
 'turning': 'turn',
 'turn': 'turning',
 'writing': 'write',
 'write': 'writing',
 'talking': 'talk',
 'talk': 'talking',
 'knowing': 'know',
 'know': 'knowing',
 'walking': 'walk',
 'walk': 'walking',
 'getting': 'get',
 'get': 'getting',
 'try

In [19]:
len(verb_third_person)

54

In [20]:
verb_third_person

{'is': 'be',
 'be': 'is',
 'has': 'have',
 'have': 'has',
 'does': 'do',
 'do': 'does',
 'says': 'say',
 'say': 'says',
 'comes': 'come',
 'come': 'comes',
 'seems': 'seem',
 'seem': 'seems',
 'goes': 'go',
 'go': 'goes',
 'faces': 'face',
 'face': 'faces',
 'makes': 'make',
 'make': 'makes',
 'wants': 'want',
 'want': 'wants',
 'takes': 'take',
 'take': 'takes',
 'gives': 'give',
 'give': 'gives',
 'appears': 'appear',
 'appear': 'appears',
 'holds': 'hold',
 'hold': 'holds',
 'gets': 'get',
 'get': 'gets',
 'follows': 'follow',
 'follow': 'follows',
 'expects': 'expect',
 'expect': 'expects',
 'requires': 'require',
 'require': 'requires',
 'believes': 'believe',
 'believe': 'believes',
 'carries': 'carry',
 'carry': 'carries',
 'intends': 'intend',
 'intend': 'intends',
 'provides': 'provide',
 'provide': 'provides',
 'adds': 'add',
 'add': 'adds',
 'succeeds': 'succeed',
 'succeed': 'succeeds',
 'reflects': 'reflect',
 'reflect': 'reflects',
 'owns': 'own',
 'own': 'owns',
 'repres

In [21]:
#Puuting verb past and past participle tenses inside a list so that we can call them randomly
verb_replacements = [verb_past,verb_present_participle,verb_third_person]

In [22]:
#Method used for introducing the gramtical perturbation in the input sentences

def read_samples_by_string(path):
    """
    1. In this method we are introducing the grammatical errors like the dropout and the replacement tokens randomly by using he 
    drop out and replacement probability of 0.25.
    2. This means with out of all the sentence in the train data 25 percent of the sentence will be grammatically incorrect as per 
    the grammatical mistakes described.
    3. The target sentence will remain as it is.
    
    :param path:path of the text data
    :return: source, target
    """
    for tokens in read_tokens(path):
        source = []
        target = []

        for token in tokens:
            target.append(token)

            # Randomly dropout some words from the input.
            dropout_token = (token in DROPOUT_TOKENS and random.random() < dropout_prob)
            replace_token = (token in REPLACEMENTS and random.random() < replacement_prob)
            replace_verb = verb_replacements[randint(0,2)]
            verb_replace_token = (token in replace_verb and random.random() < verb_replacement_prob)
            if replace_token:
                source.append(REPLACEMENTS[token])
            elif verb_replace_token:
                source.append(replace_verb[token])
            elif not dropout_token:
                source.append(token)
        yield source, target

In [23]:
max_seq_length = 50
#Returns the input and output pairs of token id
def read_samples(path):
    """
    This method with return the the encoder inputs, decoder inputs and the targets for encoder decoder model as follows:
    1. encoder inputs - This inputs will be the english sentences out of which 25 percent sentences are grammatically incorrect.
    2. target - These are the targets or the actual sentence corresponding to each input sentences.
    3. decoder inputs -  This inputs are fed to the decoder and are target inputs appended with start of sentence id at the
    starting and end of sentence id at the end as per the encoder decoder model.
    
    :param path: path of the text data
    :return: encoder_input, decoder_input,target
    """
    for source_words, target_words in read_samples_by_string(path):
        encoder_input = [convert_token_to_id(word) for word in source_words]
        encoder_pad = [PAD_ID] * (max_seq_length - len(encoder_input))
#         encoder_input = list(reversed(encoder_input + encoder_pad))
        encoder_input = list(encoder_input + encoder_pad)
        
        target = [convert_token_to_id(word) for word in target_words]
#         target.append(EOS_ID)
        target_pad = [PAD_ID] * (max_seq_length - len(target))
        target = target + target_pad
        
        decoder_input = [convert_token_to_id(word) for word in target_words]
        decoder_pad = [PAD_ID] * (max_seq_length - len(decoder_input) - 1)
        decoder_input = [GO_ID] + decoder_input + decoder_pad
        
        if(len(decoder_input) > max_seq_length):
            continue
        
        yield encoder_input, decoder_input,target

In [24]:
#Method to build dataset
def build_dataset(path):
    """
    1. This method will classify the encoder input, decoder input and the target into the respective buckets as per the size of
    sentences
    2. Here we are creating multiple copies from the processed data in order to create a larger data set for training.
    3. As we are creating multiple copies everytime the drop out and the replacement will be done randomly and so for different
    sets of sentences.
    
    :param path: path of the text file
    :return: dataset
    
    """
    dataset_enc_inp = []
    dataset_dec_inp = []
    dataset_target = []

    # Make multiple copies of the dataset so that we synthesize different
    # dropouts.
    for _ in range(dataset_copies):
        for encoder_input, decoder_input, target in read_samples(path):
            dataset_enc_inp.append(encoder_input)
            dataset_dec_inp.append(decoder_input)
            dataset_target.append(target)
    return dataset_enc_inp,dataset_dec_inp,dataset_target

In [25]:
#Building train and validation data set
encoder_input_train, decoder_input_train, target_train = build_dataset(train_path)
encoder_input_val, decoder_input_val, target_val = build_dataset(val_path)
encoder_input_test, decoder_input_test, target_test = build_dataset(test_path)

### Checking For Train and test data
Let us pick values for train and test data and check if they are as per the encoder and decoder model

### Conclusion
We can observe the following things-
1. The train and test data sets consist of 4 buckets
2. Each bucket consist of encoder input, decoder input and target according to the size of sentences.
3. The encoder inputs contain the list of id of token present in the input sentences with a grammatical mistakes in 25 percent of sentences.
4. The target consists of the original or the actual sequence or sentences corresponding to each input sentences
5. The decoder input are the target sentences appended with GO token at starting and EOS at the end corresponding to each inputs

In [26]:
tf.random.set_seed(32)

### Base Line Model

In [29]:
emb_layer = Embedding(input_dim=max_vocabulary_size,output_dim=500)

#Encoder input tensor with size (None,max_sent_length,max_vocabulary)
enc_inp = Input(shape=(max_sent_length,),name='encoder_input')
enc_emb = emb_layer(enc_inp)

#Decoder input tensor with size(NOne,None,max_vocabulary)
#Here max vocabulary is not defined because it is used in inference model
dec_inp = Input(shape=(None,),name='decoder_input')
dec_emb = emb_layer(dec_inp)

#LSTM on encoder inputs
enc_lstm = LSTM(96,return_sequences=True,return_state=True,
                kernel_initializer=tf.keras.initializers.glorot_uniform(seed=26),
                recurrent_initializer=tf.keras.initializers.orthogonal(seed=54))
enc_out, enc_memory_state, enc_carry_state  = enc_lstm(enc_emb)

#LSTM on decoder inputs
dec_lstm = LSTM(96,return_sequences=True,return_state=True,
                kernel_initializer=tf.keras.initializers.glorot_uniform(seed=26),
                recurrent_initializer=tf.keras.initializers.orthogonal(seed=54))
dec_out, dec_memory_state, dec_carry_state = dec_lstm(dec_emb,initial_state=[enc_memory_state,enc_carry_state])

#Softmax with a Time Distributed layer
dense = Dense(max_vocabulary_size, activation='softmax',
              kernel_initializer=tf.keras.initializers.glorot_uniform(seed=45),
              name='softmax_layer')
dense_time = TimeDistributed(dense, name='time_distributed_layer')
decoder_pred = dense_time(dec_out)

#Model Compilation with Adam Optimizer
model_baseline = Model(inputs=[enc_inp, dec_inp], outputs=decoder_pred)
model_baseline.compile(optimizer='rmsprop', loss='sparse_categorical_crossentropy',metrics=[perplexity])

In [42]:
model_baseline.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
decoder_input (InputLayer)      [(None, None)]       0                                            
__________________________________________________________________________________________________
encoder_input (InputLayer)      [(None, 50)]         0                                            
__________________________________________________________________________________________________
embedding (Embedding)           multiple             12322000    encoder_input[0][0]              
                                                                 decoder_input[0][0]              
__________________________________________________________________________________________________
lstm (LSTM)                     [(None, 50, 96), (No 229248      embedding[0][0]              

In [43]:
%load_ext tensorboard
logdir = os.path.join("tensorboard_log_basline")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=logdir)

In [44]:
%tensorboard --logdir tensorboard_log_basline/ --host localhost --port 5001

ERROR: Timed out waiting for TensorBoard to start. It may still be running as pid 8912.

In [49]:
model_baseline.evaluate([encoder_input_test,decoder_input_test],np.asarray(target_test))

13125/13125 [==============================] - 53s 4ms/sample - loss: 0.4411 - perplexity: 1.3684


[0.44113861468178883, 1.3684455]

In [44]:
encoder_inf_model=Model(inputs=enc_inp,outputs=[enc_out,enc_memory_state,enc_carry_state])

In [45]:
encoder_inf_model.summary()

Model: "model_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
encoder_input (InputLayer)   [(None, 50)]              0         
_________________________________________________________________
embedding (Embedding)        multiple                  1000000   
_________________________________________________________________
lstm (LSTM)                  [(None, 50, 96), (None, 9 229248    
Total params: 1,229,248
Trainable params: 1,229,248
Non-trainable params: 0
_________________________________________________________________


In [46]:
decoder_state_h=Input(shape=(96,))
decoder_state_c=Input(shape=(96,))
encoder_inf_state = Input(shape=(50,96,))
decoder_state_inputs=[decoder_state_h,decoder_state_c]

In [47]:
decoder_outputs,state_h,state_c=dec_lstm(dec_emb,initial_state=decoder_state_inputs)
decoder_states=[state_h,state_c]
decoder_inf_pred = TimeDistributed(dense)(decoder_outputs)
decoder_inf_model = Model(inputs=[dec_inp,decoder_state_h,decoder_state_c,encoder_inf_state],outputs=[decoder_inf_pred,state_h,state_c])

In [55]:
encoder_inf_model.save('Models/enc_inf.h5')

In [56]:
decoder_inf_model.save('Models/dec_inf.h5')

### Decoding Sequence - BaseLine

In [93]:
def correct_grammar():
    target_sequences = []
    for encoder_inputs in tqdm(encoder_input_test):
        enc_state,enc_h,enc_c = encoder_inf_model.predict(np.asarray([encoder_inputs]))
        decode_seq =[]
        target_word = [[GO_ID]]
        for i in range(50):
            output,state_h,state_c=decoder_inf_model.predict([np.asarray(target_word),enc_h,enc_c,enc_state])
            enc_h,enc_c = state_h,state_c
            decode_seq.append(output[0][0])
            target_word = np.argmax(output,-1)
        target_sequences.append(decode_seq)
    return target_sequences

In [ ]:
pred_sequences = correct_grammar()
y_true = tf.convert_to_tensor(target_test)
y_pred = tf.convert_to_tensor(pred_sequences)

### Categorical Loss -  BaseLine

In [98]:
scce = tf.keras.losses.SparseCategoricalCrossentropy()
loss_baseline = scce(y_true,y_pred).numpy()
print(loss_baseline)

1.8026131


### Perplexity -  BaseLine

In [100]:
perplexity_basline = K.pow(2.0,loss_baseline).numpy()
print(perplexity_basline)

3.4885151


In [101]:
model_baseline.save("Models/baseline_model.h5")

In [48]:
best = load_model('Models/model1.h5',custom_objects={'perplexity': perplexity})

In [53]:
tf.random.set_seed(32)

### Attention Model

In [84]:
emb_layer = Embedding(input_dim=max_vocabulary_size,output_dim=500)

#Encoder input tensor with size (None,max_sent_length,max_vocabulary)
enc_inp = Input(shape=(max_sent_length,),name='encoder_input')
enc_emb = emb_layer(enc_inp)
print(enc_emb[0])

#Decoder input tensor with size(NOne,None,max_vocabulary)
#Here max vocabulary is not defined because it is used in inference model
dec_inp = Input(shape=(None,),name='decoder_input')
dec_emb = emb_layer(dec_inp)
# print(dec_emb[0:1])

#LSTM on encoder inputs
enc_lstm = LSTM(96,return_sequences=True,return_state=True,
                kernel_initializer=tf.keras.initializers.glorot_uniform(seed=26),
                recurrent_initializer=tf.keras.initializers.orthogonal(seed=54))
enc_out, enc_memory_state, enc_carry_state  = enc_lstm(enc_emb)

#LSTM on decoder inputs
dec_lstm = LSTM(96,return_sequences=True,return_state=True,
                kernel_initializer=tf.keras.initializers.glorot_uniform(seed=26),
                recurrent_initializer=tf.keras.initializers.orthogonal(seed=54))

# for i in range(50):
#     dec_emb = emb_layer(dec_inp[i])
#     print(dec_emb)
#     dec_out, dec_memory_state, dec_carry_state = dec_lstm(tf.dtypes.cast(dec_emb, tf.float32),initial_state=[enc_memory_state,enc_carry_state])
#     #Attention on input and output
#     attn_layer = tf.keras.layers.Attention(name='attention_layer')
#     attn_out = attn_layer([dec_out,enc_out])

#     dec_concat_input = Concatenate(axis=-1, name='concat_layer')([dec_out, attn_out])

#     #Softmax with a Time Distributed layer
#     dense = Dense(max_vocabulary_size, activation='softmax',
#                   kernel_initializer=tf.keras.initializers.glorot_uniform(seed=45),
#                   name='softmax_layer')

#     dense_time = TimeDistributed(dense, name='time_distributed_layer')
#     decoder_pred = dense_time(dec_concat_input)
#     print(decoder_pred)

# #Model Compilation with Adam Optimizer
# model_attention = Model(inputs=[enc_inp, dec_inp], outputs=decoder_pred)
# model_attention.compile(optimizer='rmsprop', loss='sparse_categorical_crossentropy',metrics=[perplexity])

Tensor("strided_slice_55:0", shape=(50, 500), dtype=float32)


In [73]:
model_attention.summary()

Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
decoder_input (InputLayer)      [(None, None)]       0                                            
__________________________________________________________________________________________________
encoder_input (InputLayer)      [(None, 50)]         0                                            
__________________________________________________________________________________________________
embedding_3 (Embedding)         multiple             12322000    encoder_input[0][0]              
                                                                 decoder_input[0][0]              
__________________________________________________________________________________________________
lstm_6 (LSTM)                   [(None, 50, 96), (No 229248      embedding_3[0][0]          

In [42]:
%reload_ext tensorboard
logdir = os.path.join("tensorboard_attn_model_first","Model")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=logdir)

In [40]:
model_attention.fit([np.asarray(encoder_input_train),np.asarray(decoder_input_train)],np.asarray(target_train),
          epochs = 15,
          batch_size = 64,
          verbose = 1,
          validation_data=([np.asarray(encoder_input_val),np.asarray(decoder_input_val)],np.asarray(target_val)),
          callbacks=[tensorboard_callback])

In [106]:
%tensorboard --logdir tensorboard_attn_model_first/ --host localhost --port 8090

Reusing TensorBoard on port 8090 (pid 18696), started 0:01:04 ago. (Use '!kill 18696' to kill it.)

### Inference Model

In [37]:
encoder_inf_model=Model(inputs=enc_inp,outputs=[enc_out,enc_memory_state,enc_carry_state])

In [38]:
decoder_state_h=Input(shape=(96,))
decoder_state_c=Input(shape=(96,))
encoder_inf_state = Input(shape=(50,96,))
decoder_state_inputs=[decoder_state_h,decoder_state_c]

In [39]:
decoder_outputs,state_h,state_c=dec_lstm(dec_emb,initial_state=decoder_state_inputs)
decoder_states=[state_h,state_c]
attn_inf_out = attn_layer([decoder_outputs,encoder_inf_state])
decoder_concat = Concatenate(axis=-1, name='concat')([decoder_outputs, attn_inf_out])
decoder_inf_pred = TimeDistributed(dense)(decoder_concat)
decoder_inf_model = Model(inputs=[dec_inp,decoder_state_h,decoder_state_c,encoder_inf_state],outputs=[decoder_inf_pred,state_h,state_c])

In [40]:
model_attention.save("Models/model_attention_new.h5")

In [41]:
encoder_inf_model.save("Models/enc_inf_attention_new.h5")

In [42]:
decoder_inf_model.save("Models/dec_inf_attention_new.h5")

In [28]:
encoder_inf_model = load_model('Models/enc_inf_attention.h5',custom_objects={'perplexity': perplexity})

In [29]:
decoder_inf_model = load_model('Models/dec_inf_attention.h5',custom_objects={'perplexity': perplexity})

### Decoding Sequence

In [30]:
def correct_grammar():
    target_sequences = []
    for encoder_inputs in tqdm(encoder_input_test[:1500]):
        enc_state,enc_h,enc_c = encoder_inf_model.predict(np.asarray([encoder_inputs]))
        decode_seq =[]
        target_word = [[GO_ID]]
        for i in range(50):
            output,state_h,state_c=decoder_inf_model.predict([np.asarray(target_word),enc_h,enc_c,enc_state])
            enc_h,enc_c = state_h,state_c
            decode_seq.append(output[0][0])
            target_word = np.argmax(output,-1)
        target_sequences.append(decode_seq)
    return target_sequences

In [31]:
pred_sequences_attention = correct_grammar()

100%|██████████| 1500/1500 [1:44:04<00:00,  4.16s/it]


In [32]:
y_true = tf.convert_to_tensor(target_test[:1500])
y_pred = tf.convert_to_tensor(pred_sequences_attention)

In [33]:
scce = tf.keras.losses.SparseCategoricalCrossentropy()
loss_attention = scce(y_true,y_pred).numpy()

### Categorical Loss -  Attention

In [76]:
print(loss_attention)

1.7046325


### Perplexity -  Attention

In [77]:
perplexity_attention = K.pow(2.0,loss_attention).numpy()
print(perplexity_attention)

3.259459


### Additive-Attention Model

In [39]:
decoder_pred = tf.TensorArray(tf.float32, size=0, dynamic_size=True, clear_after_read=False)

emb_layer = Embedding(input_dim=max_vocabulary_size,output_dim=512)

#Encoder input tensor with size (None,max_sent_length,max_vocabulary)
enc_inp = Input(shape=(max_sent_length,),name='encoder_input')
enc_emb = emb_layer(enc_inp)

#Decoder input tensor with size(NOne,None,max_vocabulary)
#Here max vocabulary is not defined because it is used in inference model
dec_inp = Input(shape=(None,),name='decoder_input')
dec_emb = emb_layer(dec_inp)

#LSTM on encoder inputs
enc_lstm = LSTM(96,return_sequences=True,return_state=True,
                kernel_initializer=tf.keras.initializers.glorot_uniform(seed=26),
                recurrent_initializer=tf.keras.initializers.orthogonal(seed=54))
enc_out, enc_memory_state, enc_carry_state  = enc_lstm(enc_emb)

#LSTM on decoder inputs
dec_lstm = LSTM(96,return_sequences=True,return_state=True,
                kernel_initializer=tf.keras.initializers.glorot_uniform(seed=26),
                recurrent_initializer=tf.keras.initializers.orthogonal(seed=54))
#Attention on input and output
attn_layer = tf.keras.layers.AdditiveAttention()

#Softmax with a Time Distributed layer
dense = Dense(max_vocabulary_size, activation='softmax',
            kernel_initializer=tf.keras.initializers.glorot_uniform(seed=45))

memory_state = enc_memory_state
carry_state = enc_carry_state

for timestep in range(50):
    
    dec_out, dec_memory_state, dec_carry_state = dec_lstm(dec_emb[:,timestep:timestep+1],initial_state=[memory_state,carry_state])

    memory_state = dec_memory_state
    carry_state = dec_carry_state
    
    attn_out = attn_layer([dec_out,enc_out])

    dec_concat_input = Concatenate(axis=-1)([attn_out,dec_out])
    
    decoder_pred = decoder_pred.write(timestep,dense(dec_concat_input))

decoder_pred = decoder_pred.stack()
decoder_pred = tf.squeeze(decoder_pred,[2])
decoder_pred = tf.transpose(decoder_pred, perm=[1, 0, 2])


def maskedLoss(y_true, y_pred):
    #getting mask value
    mask = tf.math.logical_not(tf.math.equal(y_true, 0)) 
    #calculating the loss
    scce = tf.keras.losses.SparseCategoricalCrossentropy(reduction=tf.keras.losses.Reduction.NONE)
    loss_ = scce(y_true, y_pred)
#     loss_ = loss_function(y_true, y_pred) 
    #converting mask dtype to loss_ dtype
    mask = tf.cast(mask, dtype=loss_.dtype) 
    #applying the mask to loss 
    loss_ = loss_*mask 
    #getting mean over all the values 
    loss_ = tf.reduce_mean(loss_) 
    return loss_

def maskedPerplexity(y_true, y_pred):
    #getting mask value
    mask = tf.math.logical_not(tf.math.equal(y_true, 0)) 
    #calculating the loss
    scce = tf.keras.losses.SparseCategoricalCrossentropy(reduction=tf.keras.losses.Reduction.NONE)
    loss_ = scce(y_true, y_pred)
#     loss_ = loss_function(y_true, y_pred) 
    #converting mask dtype to loss_ dtype
    mask = tf.cast(mask, dtype=loss_.dtype) 
    #applying the mask to loss 
    loss_ = loss_*mask 
    #getting mean over all the values 
    loss_ = tf.reduce_mean(loss_) 
    return K.pow(2.0,loss_)

#Model Compilation with Adam Optimizer
model_additive_attention = Model(inputs=[enc_inp, dec_inp], outputs=decoder_pred)
model_additive_attention.compile(optimizer='rmsprop', loss=[maskedLoss],metrics=[maskedPerplexity])

In [29]:
def maskedLoss(y_true, y_pred):
    #getting mask value
    mask = tf.math.logical_not(tf.math.equal(y_true, 0)) 
    #calculating the loss
    scce = tf.keras.losses.SparseCategoricalCrossentropy(reduction=tf.keras.losses.Reduction.NONE)
    loss_ = scce(y_true, y_pred)
#     loss_ = loss_function(y_true, y_pred) 
    #converting mask dtype to loss_ dtype
    mask = tf.cast(mask, dtype=loss_.dtype) 
    #applying the mask to loss 
    loss_ = loss_*mask 
    #getting mean over all the values 
    loss_ = tf.reduce_mean(loss_) 
    return loss_

def maskedPerplexity(y_true, y_pred):
    #getting mask value
    mask = tf.math.logical_not(tf.math.equal(y_true, 0)) 
    #calculating the loss
    scce = tf.keras.losses.SparseCategoricalCrossentropy(reduction=tf.keras.losses.Reduction.NONE)
    loss_ = scce(y_true, y_pred)
#     loss_ = loss_function(y_true, y_pred) 
    #converting mask dtype to loss_ dtype
    mask = tf.cast(mask, dtype=loss_.dtype) 
    #applying the mask to loss 
    loss_ = loss_*mask 
    #getting mean over all the values 
    loss_ = tf.reduce_mean(loss_) 
    return K.pow(2.0,loss_)

In [41]:
tf.shape(enc_out)

<tf.Tensor 'Shape:0' shape=(3,) dtype=int32>

In [41]:
model_additive_attention.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
decoder_input (InputLayer)      [(None, None)]       0                                            
__________________________________________________________________________________________________
encoder_input (InputLayer)      [(None, 50)]         0                                            
__________________________________________________________________________________________________
embedding (Embedding)           multiple             12617728    encoder_input[0][0]              
                                                                 decoder_input[0][0]              
__________________________________________________________________________________________________
tf_op_layer_strided_slice (Tens [(None, None, 512)]  0           embedding[1][0]              

In [42]:
%reload_ext tensorboard
logdir = os.path.join("tensorboard_additive_attention","Model")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir=logdir)

In [43]:
model_additive_attention.fit([np.asarray(encoder_input_train),np.asarray(decoder_input_train)],np.asarray(target_train),
          epochs = 20,
          batch_size = 64,
          verbose = 1,
          validation_data=([np.asarray(encoder_input_val),np.asarray(decoder_input_val)],np.asarray(target_val)),
          callbacks=[tensorboard_callback])

Train on 33883 samples, validate on 4307 samples
Epoch 1/20
33883/33883 [==============================] - 3383s 100ms/sample - loss: 2.1867 - maskedPerplexity: 4.6873 - val_loss: 1.7357 - val_maskedPerplexity: 3.4104
Epoch 2/20
33883/33883 [==============================] - 2904s 86ms/sample - loss: 1.8084 - maskedPerplexity: 3.5275 - val_loss: 1.5426 - val_maskedPerplexity: 2.9766
Epoch 3/20
33883/33883 [==============================] - 2880s 85ms/sample - loss: 1.6161 - maskedPerplexity: 3.0832 - val_loss: 1.4245 - val_maskedPerplexity: 2.7378
Epoch 4/20
33883/33883 [==============================] - 2853s 84ms/sample - loss: 1.4560 - maskedPerplexity: 2.7552 - val_loss: 1.2879 - val_maskedPerplexity: 2.4852
Epoch 5/20
33883/33883 [==============================] - 2877s 85ms/sample - loss: 1.2956 - maskedPerplexity: 2.4647 - val_loss: 1.1591 - val_maskedPerplexity: 2.2683
Epoch 6/20
33883/33883 [==============================] - 2857s 84ms/sample - loss: 1.1401 - maskedPerplexity:

In [52]:
%tensorboard --logdir tensorboard_additive_attention/ --host localhost --port 8087

ERROR: Timed out waiting for TensorBoard to start. It may still be running as pid 7504.

### Inference Model

In [44]:
encoder_inf_model=Model(inputs=enc_inp,outputs=[enc_out,enc_memory_state,enc_carry_state])

In [45]:
decoder_state_h=Input(shape=(96,))
decoder_state_c=Input(shape=(96,))
encoder_inf_state = Input(shape=(50,96,))
decoder_state_inputs=[decoder_state_h,decoder_state_c]

In [46]:
decoder_outputs,state_h,state_c=dec_lstm(dec_emb,initial_state=decoder_state_inputs)
decoder_states=[state_h,state_c]
attn_inf_out = attn_layer([decoder_outputs,encoder_inf_state])
decoder_concat = Concatenate(axis=-1, name='concat')([attn_inf_out,decoder_outputs])
decoder_inf_pred = dense(decoder_concat)
decoder_inf_model = Model(inputs=[dec_inp,decoder_state_h,decoder_state_c,encoder_inf_state],outputs=[decoder_inf_pred,state_h,state_c])

In [46]:
decoder_inf_model.summary()

Model: "model_2"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
decoder_input (InputLayer)      [(None, None)]       0                                            
__________________________________________________________________________________________________
embedding (Embedding)           multiple             12617728    decoder_input[0][0]              
__________________________________________________________________________________________________
input_1 (InputLayer)            [(None, 96)]         0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 96)]         0                                            
____________________________________________________________________________________________

In [47]:
model_additive_attention.save("Models/model_add_attn.h5")

In [48]:
encoder_inf_model.save("Models/enc_inf_add_attn.h5")

In [49]:
decoder_inf_model.save("Models/dec_inf_add_attn.h5")

### Decoding Sequence

In [30]:
encoder_inf_model = load_model('Models/enc_inf_add_attn_final.h5',custom_objects={'maskedLoss': maskedLoss,'maskedPerplexity': maskedPerplexity})

In [31]:
decoder_inf_model = load_model('Models/dec_inf_add_attn_final.h5',custom_objects={'maskedLoss': maskedLoss,'maskedPerplexity': maskedPerplexity})

In [31]:
def correct_grammar(raw_data):
    target_sequences = []
    for encoder_inputs in tqdm(raw_data):
        enc_state,enc_h,enc_c = encoder_inf_model.predict(np.asarray([encoder_inputs]))
        decode_seq =[]
        target_word = [[GO_ID]]
        while True:
            output,state_h,state_c=decoder_inf_model.predict([np.asarray(target_word),enc_h,enc_c,enc_state])
            enc_h,enc_c = state_h,state_c
            target_word = np.argmax(output,-1)
            decode_seq.append(convert_id_to_token(target_word[0,0]))
            if target_word==EOS_ID:
                break
            elif len(decode_seq) > len(encoder_inputs) + 2:
                break
        target_sequences.append(decode_seq)
    return target_sequences

In [55]:
pred_sequences_attention = correct_grammar(encoder_input_test)

100%|██████████| 1500/1500 [18:34<00:00,  1.35it/s]


In [58]:
np.argmax(pred_sequences_attention[:1],-1)

array([[207,   4,  10, 406,   6,   2]], dtype=int64)

In [66]:
size =[]
for pred_sequence in pred_sequences_attention:
    size.append(len(pred_sequence))

In [72]:
np.percentile(size, 100)

80.0

In [64]:
losses = []
for i in tqdm(range(1500)):
    if(len(pred_sequences_attention[i])>38):
        continue
    target_test[i] = target_test[i][:target_test[i].index(2)+1]
    if len(pred_sequences_attention[i]) > len(target_test[i]):
        target_test[i] = target_test[i] + [PAD_ID] * (len(pred_sequences_attention[i])-len(target_test[i]))
    elif len(pred_sequences_attention[i]) < len(target_test[i]):
        continue
#         pred_sequences_attention[i] = pred_sequences_attention[i] + [[to_categorical([PAD_ID],num_classes=24644)]] * (len(target_test[i])-len(pred_sequences_attention[i]))
    y_true = tf.convert_to_tensor(target_test[i])
    y_pred = tf.convert_to_tensor(pred_sequences_attention[i])
    mask = tf.math.logical_not(tf.math.equal(y_true, 0)) 
    #calculating the loss
    scce = tf.keras.losses.SparseCategoricalCrossentropy(reduction=tf.keras.losses.Reduction.NONE)
    loss_ = scce(y_true, y_pred)
    mask = tf.cast(mask, dtype=loss_.dtype) 
    loss_ = loss_*mask 
    loss_ = tf.reduce_mean(loss_) 
    losses.append(loss_)

In [96]:
len(losses)

1026

In [90]:
convert_id_to_token(1188)

'matters'

In [75]:
y_true = tf.convert_to_tensor(target_test[:1500])
y_pred = tf.convert_to_tensor(pred_sequences_attention)

In [62]:
scce = tf.keras.losses.SparseCategoricalCrossentropy()
loss_attention = scce(y_true,y_pred).numpy()

### Categorical Loss -  Attention

In [100]:
print(np.sum(losses)/len(losses))

2.952999836287768


### Perplexity -  Attention

In [101]:
perplexity_attention = K.pow(2.0,np.sum(losses)/len(losses)).numpy()
print(perplexity_attention)

7.743575


## Compute BLEU Score

### Get Sequence

In [27]:
def predict_sequence(raw_data):
    target_sequences = []
    for encoder_inputs in tqdm(raw_data):
        enc_state,enc_h,enc_c = encoder_inf_model.predict(np.asarray([encoder_inputs]))
        decode_seq =[]
        target_word = [[GO_ID]]
        while True:
            output,state_h,state_c=decoder_inf_model.predict([np.asarray(target_word),enc_h,enc_c,enc_state])
            enc_h,enc_c = state_h,state_c
            target_word = np.argmax(output,-1)
            decode_seq.append(convert_id_to_token(target_word[0,0]))
            if target_word==EOS_ID:
                break
            elif len(decode_seq) > len(encoder_inputs) + 2:
                break
        target_sequences.append(decode_seq)
    return target_sequences

### BLEU Logic

In [32]:
def get_BLEU_sequences(output_seq):
    reference_sequence = []
    for sentence in output_seq:
        ref_seq = []
        for word in sentence:
            if word == PAD_ID:
                break
            ref_seq.append(convert_id_to_token(word))
        reference_sequence.append([ref_seq])
    return reference_sequence

#### Train BLEU Score

In [34]:
pred_sequences_train = predict_sequence(encoder_input_train[0:1])

100%|██████████| 1/1 [00:01<00:00,  1.55s/it]


In [36]:
pred_sequences_train

[['book', 'i', '.', 'EOS']]

In [35]:
train_reference = get_BLEU_sequences(target_train[0:1])

In [37]:
train_reference

[[['book', 'i', '.', 'EOS']]]

In [38]:
score_bigarm_train = corpus_bleu(train_reference, pred_sequences_train,weights=(0, 1, 0, 0))
score_cumm_ngram_train = corpus_bleu(train_reference, pred_sequences_train,weights=(0.25, 0.25, 0.25, 0.25))

In [39]:
print("Train BLEU score for bigram: "+str(score_bigarm_train))
print("Train BLEU score for cummilative ngram: "+str(score_cumm_ngram_train))

Train BLEU score for bigram: 1.0
Train BLEU score for cummilative ngram: 1.0


#### Validation BLEU Score

In [67]:
pred_sequences_val = predict_sequence(encoder_input_val)

100%|██████████| 4307/4307 [54:15<00:00,  1.32it/s]  


In [68]:
val_reference = get_BLEU_sequences(target_val)

In [81]:
score_bigarm_val = corpus_bleu(val_reference, pred_sequences_val,weights=(0, 1, 0, 0))
score_cumm_ngram_val = corpus_bleu(val_reference, pred_sequences_val,weights=(0.25, 0.25, 0.25, 0.25))

In [82]:
print("Validation BLEU score for bigram: "+str(score_bigarm_val))
print("Validation BLEU score for cummilative ngram: "+str(score_cumm_ngram_val))

Validation BLEU score for bigram: 0.6457648043055508
Validation BLEU score for cummilative ngram: 0.5737510149490748


#### Test BLEU Score

In [77]:
pred_sequences_test = correct_grammar(encoder_input_test)

100%|██████████| 4387/4387 [48:19<00:00,  1.51it/s]  


In [83]:
test_reference = get_BLEU_sequences(target_test)

In [87]:
score_bigarm_test = corpus_bleu(test_reference, pred_sequences_test,weights=(0, 1, 0, 0))
score_cumm_ngram_test = corpus_bleu(test_reference, pred_sequences_test,weights=(0.25, 0.25, 0.25, 0.25))

In [88]:
print("Validation BLEU score for bigram: "+str(score_bigarm_test))
print("Validation BLEU score for cummilative ngram: "+str(score_cumm_ngram_test))

Validation BLEU score for bigram: 0.5913185431655771
Validation BLEU score for cummilative ngram: 0.5110530964182455


## BLEU Input And Output

In [28]:
train_input = get_BLEU_sequences(encoder_input_train)

In [33]:
train_output = get_BLEU_sequences(target_train)

In [45]:
score_bigarm_train = corpus_bleu(train_input[0:5], train_output[0:5],weights=(0, 1, 0, 0))
score_cumm_ngram_train = corpus_bleu(train_input[0:5], train_output[0:5],weights=(0.25, 0.25, 0.25, 0.25))

TypeError: unhashable type: 'list'

In [36]:
print("Validation BLEU score for bigram: "+str(score_bigarm_test))
print("Validation BLEU score for cummilative ngram: "+str(score_cumm_ngram_test))

In [40]:
train_input[0:5]

[['book', 'i', '.'],
 ['chapter', 'i', '.'],
 ['i', 'doing', 'not', 'mean', 'to', 'describe', 'myself', '.'],
 ['already',
  'i',
  'feel',
  'that',
  'the',
  'personal',
  'pronoun',
  'will',
  'appears',
  'too',
  'often',
  'in',
  'these',
  'pages',
  '.'],
 ['knowing',
  'faults',
  'of',
  'my',
  'character',
  'almost',
  'as',
  'well',
  'as',
  'my',
  'best',
  'friends',
  'know',
  'them',
  ',',
  'i',
  'shall',
  'attempt',
  'to',
  'hide',
  'them',
  'no',
  'more',
  'than',
  'would',
  'those',
  'beloved',
  'ones',
  '.']]

In [41]:
train_output[0:5]

[[['book', 'i', '.']],
 [['chapter', 'i', '.']],
 [['i', 'do', 'not', 'mean', 'to', 'describe', 'myself', '.']],
 [['already',
   'i',
   'feel',
   'that',
   'the',
   'personal',
   'pronoun',
   'will',
   'appear',
   'too',
   'often',
   'in',
   'these',
   'pages',
   '.']],
 [['knowing',
   'the',
   'faults',
   'of',
   'my',
   'character',
   'almost',
   'as',
   'well',
   'as',
   'my',
   'best',
   'friends',
   'know',
   'them',
   ',',
   'i',
   'shall',
   'attempt',
   'to',
   'hide',
   'them',
   'no',
   'more',
   'than',
   'would',
   'those',
   'beloved',
   'ones',
   '.']]]